In [1]:
import pandas as pd
import os
import random
import time
import numpy as np
from IPython.core.display import HTML, Markdown
from datetime import datetime
from matplotlib import pyplot as plt
import re
import sqlite3
from extractor import Extractor
import numpy as np
from IPython.display import clear_output

db_path = '/media/princio/ssd512/stratosphere/db_3.sqlite3'
dirs = {
    'malware': '/media/princio/ssd512/stratosphere/pcap/csv/malware/',
    'normal': '/media/princio/ssd512/stratosphere/pcap/csv/normal/'
}

try:
    pcap_dict
except NameError:
    pcap_dict = {'normal':{}, 'botnet':{}}
    
try:
    pcap_names
except NameError:
    pcap_names = {'normal':{}, 'botnet':{}}

def get_type(pcapname):
    bot_path = os.path.join(dirs['malware'], pcapname)
    nor_path = os.path.join(dirs['normal'], pcapname)
    if os.path.exists(bot_path):
        type_='botnet'
        df_path = bot_path
    elif os.path.exists(nor_path):
        type_='normal'
        df_path = nor_path
    else:
        return None
    return type_, df_path
    
def get_df(pcapname, reload=False):
    if reload:
        type_, df_path = get_type(pcapname)
        pcap_dict[type_][pcapname] = pd.read_csv(df_path, usecols=list(range(0,12)))
        return pcap_dict[type_][pcapname]
    
    if pcapname in pcap_dict['botnet']:
        return pcap_dict['botnet'][pcapname]
    if pcapname in pcap_dict['normal']:
        return pcap_dict['normal'][pcapname]
    
    type_, df_path = get_type(pcapname)
    pcap_dict[type_][pcapname] = pd.read_csv(df_path, usecols=list(range(0,12)))
    return pcap_dict[type_][pcapname].copy()



In [7]:
import plotly.express as px
df = get_df('42_botnet-capture-20110810-neris.pcap.csv')

df['esito'] = df['dns.flags.rcode'].apply(lambda x: 'no-resp' if np.isnan(x) else 'resp-ok' if x == 0 else 'no-such-name' if x == 3 else 'resp-err')
df['dns.time'] = df['dns.time'].fillna(0.1)
fig = px.scatter(df, x="frame.time_epoch_req", y="nosfx_0.1", color="esito",
                 size='dns.time', hover_data=['dns.qry.type'])
fig.show()

In [44]:

import dash
import dash_core_components as dcc
import dash_html_components as html
import dash_table
from dash.dependencies import Input, Output
from plotly.subplots import make_subplots

db = sqlite3.connect(db_path)
df = pd.read_sql('SELECT * from pcap', db).drop(columns=['id', 's_id', 's_win'])
db.close()

app = dash.Dash(__name__)

df['id'] = df['name']

app.layout = html.Div([
    dash_table.DataTable(
        id='datatable-interactivity',
        columns=[
            {"name": i, "id": i, "deletable": True, "selectable": True} for i in df.columns if i != 'id'
        ],
        data=df.to_dict('records'),
        filter_action="native",
        sort_action="native",
        sort_mode="multi",
        column_selectable="single",
        row_selectable="multi",
        row_deletable=True,
        selected_columns=[],
        selected_rows=[],
        page_action="native",
        page_current= 0,
        page_size= 10
    ),
    html.Div(id='datatable-interactivity-container')
])


@app.callback(
    Output('datatable-interactivity', 'style_data_conditional'),
    Input('datatable-interactivity', 'selected_columns')
)
def update_styles(selected_columns):
    return [{
        'if': { 'column_id': i },
        'background_color': '#D2F3FF'
    } for i in selected_columns]


@app.callback(
    Output('datatable-row-ids-container', 'children'),
    Input('datatable-row-ids', 'derived_virtual_row_ids'),
    Input('datatable-row-ids', 'selected_row_ids'),
    Input('datatable-row-ids', 'active_cell'))
def update_graphs(row_ids, selected_row_ids, active_cell):
    # When the table is first rendered, `derived_virtual_data` and
    # `derived_virtual_selected_rows` will be `None`. This is due to an
    # idiosyncrasy in Dash (unsupplied properties are always None and Dash
    # calls the dependent callbacks when the component is first rendered).
    # So, if `rows` is `None`, then the component was just rendered
    # and its value will be the same as the component's dataframe.
    # Instead of setting `None` in here, you could also set
    # `derived_virtual_data=df.to_rows('dict')` when you initialize
    # the component.
    
    #######################   ROWS  #################################
    selected_id_set = set(selected_row_ids or [])

    if row_ids is None:
        dff = df
        # pandas Series works enough like a list for this to be OK
        row_ids = df['id']
    else:
        dff = df.loc[row_ids]

    active_row_id = active_cell['row_id'] if active_cell else None
    
    colors = []
    for id in row_ids:
        colors.append('#FF69B4' if id == active_row_id
              else '#7FDBFF' if id in selected_id_set
              else '#0074D9')

    #######################   ROWS  #################################
    
    fig = make_subplots(rows=4, shared_xaxes=True, vertical_spacing=0)
    
    for i, column in enumerate(["tot", "uniques/tot", "response-ok", "no-such-name"]):
        if column in dff:
            dff_bot = dff[dff['type'] == 'botnet']
            fig.add_bar(name=column, x=dff["name"], y=dff[column], marker={'color': colors}, row=i+1, col=1)
            fig['layout'][f'yaxis{"" if i==0 else i+1}'].update(title=column)
    
    fig['layout'].update(showlegend=False, margin={"t": 10, "l": 10, "r": 10}, xaxis={"automargin": True}, height=250*4)
    
    print(fig)
    return dcc.Graph(figure=fig)
    return [
        dcc.Graph(
            id=column,
            figure={
                "data": [
                    {
                        "x": dff["name"],
                        "y": dff[column],
                        "type": "bar",
                        "marker": {"color": colors},
                    }
                ],
                "layout": {
                    "xaxis": {"automargin": True},
                    "yaxis": {
                        "automargin": True,
                        "title": {"text": column}
                    },
                    "height": 250,
                    "margin": {"t": 10, "l": 10, "r": 10},
                },
            },
        )
        # check if column exists - user may have deleted it
        # If `column.deletable=False`, then you don't
        # need to do this check.
        for column in ["tot", "uniques/tot", "response-ok", "no-such-name"] if column in dff
    ]

if __name__ == '__main__':
    app.run_server(debug=False)


Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is run

 * Running on http://127.0.0.1:8050/ (Press CTRL+C to quit)
127.0.0.1 - - [06/Apr/2021 13:09:26] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [06/Apr/2021 13:09:26] "GET /_dash-dependencies HTTP/1.1" 200 -
127.0.0.1 - - [06/Apr/2021 13:09:26] "GET /_dash-layout HTTP/1.1" 200 -
127.0.0.1 - - [06/Apr/2021 13:09:26] "GET /_favicon.ico?v=1.19.0 HTTP/1.1" 200 -
127.0.0.1 - - [06/Apr/2021 13:09:26] "POST /_dash-update-component HTTP/1.1" 200 -


In [ ]:

import dash
import dash_core_components as dcc
import dash_html_components as html
import dash_table
from dash.dependencies import Input, Output
from plotly.subplots import make_subplots

db = sqlite3.connect(db_path)
df = pd.read_sql('SELECT * from pcap', db).drop(columns=['id', 's_id', 's_win'])
df['id'] = df['name']
db.close()

app = dash.Dash(__name__)

df['id'] = df['name']

app.layout = html.Div([
    dash_table.DataTable(
        id='datatable-row-ids',
        columns=[
            {"name": i, "id": i, "deletable": True, "selectable": True} for i in df.columns if i != 'id'
        ],
        data=df.to_dict('records'),
        filter_action="native",
        sort_action="native",
        sort_mode="multi",
        column_selectable="single",
        row_selectable="multi",
        row_deletable=True,
        selected_columns=[],
        selected_rows=[],
        page_action="native",
        page_current= 0,
        page_size= 10
    ),
    html.Div(id='datatable-row-ids-container')
])


@app.callback(
    Output('datatable-interactivity', 'style_data_conditional'),
    Input('datatable-interactivity', 'selected_columns')
)
def update_styles(selected_columns):
    return [{
        'if': { 'column_id': i },
        'background_color': '#D2F3FF'
    } for i in selected_columns]


@app.callback(
    Output('datatable-row-ids-container', 'children'),
    Input('datatable-row-ids', 'derived_virtual_row_ids'),
    Input('datatable-row-ids', 'selected_row_ids'),
    Input('datatable-row-ids', 'active_cell'))
def update_graphs(row_ids, selected_row_ids, active_cell):
    # When the table is first rendered, `derived_virtual_data` and
    # `derived_virtual_selected_rows` will be `None`. This is due to an
    # idiosyncrasy in Dash (unsupplied properties are always None and Dash
    # calls the dependent callbacks when the component is first rendered).
    # So, if `rows` is `None`, then the component was just rendered
    # and its value will be the same as the component's dataframe.
    # Instead of setting `None` in here, you could also set
    # `derived_virtual_data=df.to_rows('dict')` when you initialize
    # the component.
    
    #######################   ROWS  #################################
    selected_id_set = set(selected_row_ids or [])

    if row_ids is None:
        dff = df
        # pandas Series works enough like a list for this to be OK
        row_ids = df['id']
    else:
        dff = df.loc[row_ids]

    active_row_id = active_cell['row_id'] if active_cell else None
    
    colors = []
    for id in row_ids:
        colors.append('#FF69B4' if id == active_row_id
              else '#7FDBFF' if id in selected_id_set
              else '#0074D9')
    return [
            dcc.Graph(
                id=column + '--row-ids',
                figure={
                    'data': [
                        {
                            'x': dff['country'],
                            'y': dff[column],
                            'type': 'bar',
                            'marker': {'color': colors},
                        }
                    ],
                    'layout': {
                        "xaxis": {"automargin": True, 'visible':(i+1==len([c for c in ["tot", "uniques/tot", "response-ok", "no-such-name"] if column in dff]))},
                        'yaxis': {
                            'automargin': True,
                            'title': {'text': column}
                        },
                        'height': 250,
                        'margin': {'t': 10, 'l': 10, 'r': 10},
                    },
                },
            )
            # check if column exists - user may have deleted it
            # If `column.deletable=False`, then you don't
            # need to do this check.
            for column in ['pop', 'lifeExp', 'gdpPercap'] if column in dff
        ]
    return [
        dcc.Graph(
            id=column + '--row-ids',
            figure={
                "data": [
                    {
                        "x": dff["name"],
                        "y": dff[column],
                        "type": "bar",
                        "marker": {"color": colors},
                    }
                ],
                "layout": {
                    "xaxis": {"automargin": True, 'visible':(i==len([c for c in ["tot", "uniques/tot", "response-ok", "no-such-name"] if column in dff]))},
                    "yaxis": {
                        "automargin": True,
                        "title": {"text": column}
                    },
                    "height": 250,
                    "margin": {"t": 10, "l": 10, "r": 10},
                },
            },
        )
        for i, column in enumerate(["tot", "uniques/tot", "response-ok", "no-such-name"]) if column in dff
    ]

if __name__ == '__main__':
    app.run_server(debug=False)


id                                      name    type   s_id  s_win  \
0      1    355-1_2018-05-07_capture-win6.pcap.csv  botnet  355-1   win6   
1      2       226-1_2017-2-27_win5.fixed.pcap.csv  botnet  226-1   win5   
2      3  31-1_2013-11-25_capture-win10-2.pcap.csv  botnet   31-1  win10   
3      4     226-2_2017-02-27_win16.fixed.pcap.csv  botnet  226-2  win16   
4      5    150-1_2015-12-05_capture-win3.pcap.csv  botnet  150-1   win3   
..   ...                                       ...     ...    ...    ...   
422  423         157-1_2015-05-01_linux-1.pcap.csv  botnet   None   None   
423  424              314-1_capture_win13.pcap.csv  botnet  314-1  win13   
424  425              312-1_capture_win11.pcap.csv  botnet  312-1  win11   
425  426               310-1_capture_win9.pcap.csv  botnet  310-1   win9   
426  427              254-1_capture_win13.pcap.csv  botnet  254-1  win13   

         tot  uniques  uniques/tot   days         qry/h  no-response  \
0    4301260     1005     0.000234   6.80  2.634624e+04       896886   
1    2570863      592     0.000230  24.61  4.351190e+03        16248   
2    2084028     1040     0.000499   7.73  1.122071e+04        47636   
3    1904514      592     0.000311  18.63  4.258605e+03        11024   
4    1724733      402     0.000233  31.87  2.254483e+03       212322   
..       ...      ...          ...    ...           ...          ...   
422        2        1     0.500000   0.00  7.346939e+07            0   
423        2        1     0.500000   0.00  3.643909e+05            0   
424        2        1     0.500000   0.00  1.055100e+05            0   
425        2        1     0.500000   0.00  3.609203e+05            0   
426        2        1     0.500000   0.00  3.799472e+06            0   

     response-ok  response-error  no-such-name  legit_list  
0        1556463         1847911       1824480          94  
1        1647682          906933        876648     1435762  
2        1841032          195360        195358     1841306  
3        1227550          665940        645489     1073396  
4          44545         1467866       1436855          14  
..           ...             ...           ...         ...  
422            2               0             0           2  
423            2               0             0           2  
424            2               0             0           2  
425            2               0             0           2  
426            2               0             0           2  

[427 rows x 15 columns]